In [1]:
import glob
import pandas as pd
import re
import tensorflow as tf
from collections import Counter
import numpy as np
count = Counter()

In [2]:
filenames1 = []
for filename in glob.glob('Systemy_dialogowe/data/*.tsv'):
    filenames1.append(filename)

In [3]:
def prep(filenames):
    df = pd.DataFrame(columns=['Rola', 'Wypowiedź', 'Act'])
    for filename in filenames:
        temp = pd.read_csv(filename, sep='\t', names=["Rola", "Wypowiedź", "Act"])
        df = pd.concat([df, temp], ignore_index=True)
    return df

In [4]:
df = prep(filenames1)
df = df.loc[df['Rola'] == 'user']
df = df.fillna('null')
df

Rola                    Wypowiedź                                    Act
1     user                        Witam                                hello()
3     user   Co możesz dla mnie zrobić?                                 help()
5     user   Jakie są moje repozytoria?                         request(repos)
7     user  ok. co nowego w Zajęcia AI?  affirm() & request(repo = Zajecia AI)
9     user                  Tylko tyle?                              reqmore()
...    ...                          ...                                    ...
1409  user               upewniam się                                     null
1411  user           pokaż mi raport                             request(repo)
1414  user                    zmienić                                     null
1416  user                       Tak                                       ack
1466  user                          elo                                hello()

[585 rows x 3 columns]

In [5]:
df['Act'].unique()

array(['hello()', 'help()', 'request(repos)',
       'affirm() & request(repo = Zajecia AI)', 'reqmore()',
       'request(notifications)', 'request(notification = 1)',
       'request(link)', 'affirm() & reqmore()',
       'request(repo = Projekt – Sklep)', 'request(issues)', 'ack()',
       'request(commits = mattyl34)', 'request(commits = -5)',
       'affirm() & request(repo = Gra - kółko i krzyżyk)', 'thankyou()',
       'inform()', 'helpresponse()', 'request(repo = Zajecia AI)',
       'request(delete)', 'ack() & inform()',
       'request(repo = Projekt-sklep)', 'request(files = 1:3)',
       'request()', 'bye()', 'request(file)',
       'helpresponse() & request(repo)', 'request(command)',
       'request(repo = Projekt - Sklep)', 'request(authors)',
       'request(Bob)', 'request(repo = system)',
       'request(repo = super_stronka_internetowa)',
       'request(date, pr = 2)', 'request(repo = nazwaRepozytorium)',
       'request(repo = zadania)', 'request(author, pr = 1)',


### split by &
### ignore args and ()
### {'request', 'inform', 'bye', 'reqmore', 'help', 'ack', 'affirm', 'hello', 'thankyou', 'null'}

In [6]:
new = pd.DataFrame(columns=['Wypowiedź', 'Act'])
values = set()
for index, row in df.iterrows():
    act = row[2].split('&')
    act = [re.sub('\(.*\)', '', x) for x in act]
    act = [re.sub(' ', '', x) for x in act]
    act = [re.sub('helpresponse', 'help', x) for x in act]
    [values.add(x) for x in act]
    temp = pd.DataFrame({'Wypowiedź':row[1], 'Act': act})
    new = pd.concat([new, temp], ignore_index=True)
new.head(10)
print(values)

{'help', 'reqmore', 'bye', 'thankyou', 'hello', 'affirm', 'ack', 'inform', 'request', 'null'}


In [7]:
unique = ['request', 'inform', 'bye', 'reqmore', 'help', 'ack', 'affirm', 'hello', 'thankyou', 'null']
sorted_values = {}
for item in unique:
    temp = new.loc[new['Act'] == item]
#     print(new.loc[new['Act'] == item])
    sorted_values[item] = temp
    temp.to_csv(f'data_sorted//{item}', sep='\t', index=False)
sorted_values

{'request':                                 Wypowiedź      Act
 2              Jakie są moje repozytoria?  request
 4             ok. co nowego w Zajęcia AI?  request
 6          Mam jakieś nowe powiadomienia?  request
 8           Opowiedz mi o powiadomieniu 1  request
 9    Podaj mi linka do tego powiadomienia  request
 ..                                    ...      ...
 571                    Próbuję ponownie    request
 573                             próbuję    request
 577           pokaż mi raport projektu     request
 584           pokaż mi raport projektu     request
 587                    pokaż mi raport     request
 
 [130 rows x 2 columns],
 'inform':                    Wypowiedź     Act
 26               to wszystko  inform
 33       Oki, to będzie tyle  inform
 76   To nie, to już wszystko  inform
 103     moja gałąź, "master"  inform
 104                  moja PR  inform
 ..                       ...     ...
 535                 gGphJD    inform
 545                  qG

In [8]:
def preprocess(line):
    txt = line
    txt = re.sub(
        "(£|§|!|@|#|\$|%|\^|&|\*|\(|\)|_|-|\+|=|\{|\[|\}|\]|:|;|\"|'|\|\\|\<|,|\>|\.|\?|/|~|`|\|–|–|)",
        "",
        txt,
    )
    txt = txt.lower()
    txt = re.sub("[0-9]", "", txt)
    txt = re.sub("[ \t]+", " ", txt)
    txt = re.sub(" +$", "", txt)
    txt = re.sub("ą", "a", txt)
    txt = re.sub("ć", "c", txt)
    txt = re.sub("ę", "e", txt)
    txt = re.sub("ł", "l", txt)
    txt = re.sub("ń", "n", txt)
    txt = re.sub("ó", "o", txt)
    txt = re.sub("ś", "s", txt)
    txt = re.sub("ź", "z", txt)
    txt = re.sub("ż", "z", txt)
    words = txt.split()
    words = [w[:6] if len(w) > 6 else w for w in words]
    out = []
    for word in words:
#         if word not in stopwords:
          out.append(word)
    for stem in out:
        count[stem] += 1
    text = " ".join(out)
#     print(text)
    return text


In [9]:
from tensorflow.keras.utils import to_categorical
from numpy import argmax

acts = ['inform', 'reqmore', 'thankyou', 'ack', 'affirm', 'hello', 'request', 'help', 'null', 'bye']
to_num = {act: idx for idx, act in enumerate(acts)}

In [10]:
prep = pd.DataFrame(columns=['Wypowiedź', 'Act'])
values = set()
max_len = 0
for index, row in new.iterrows():
    temp = preprocess(row[0])
    one_hot_encode = to_categorical(to_num[row[1]], num_classes=len(acts))
#     one_hot_encode = np.asarray(one_hot_encode).astype('float32')
    max_len = max(max_len, len(temp))
    frame = pd.DataFrame({'Wypowiedź': temp, 'Act': [np.asarray(one_hot_encode).astype('float32')]})
    prep = pd.concat([prep, frame], ignore_index=True)
# print(prep)
max_len

53

In [11]:
prep = prep.sample(frac=1).reset_index(drop=True)
prep

Wypowiedź  \
0                                     czesc   
1                          chcial odrzuc pr   
2                                    capric   
3                        oki to bedzie tyle   
4                                    qgphjd   
..                                      ...   
586  wyjasn mi komend pokaz mi liste komend   
587                        wyjasn mi komend   
588                           zmieni konfig   
589                                  ggphjd   
590                      chce zmieni konfig   

                                                   Act  
0    [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...  
1    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, ...  
2    [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
3    [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
4    [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
..                                                 ...  
586  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, ...  
587  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, ...  
588  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, ...  
589  [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
590  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, ...  

[591 rows x 2 columns]

In [12]:
num_words = 130

for item in count.most_common(num_words):
    print(item)

('mi', 219)
('pokaz', 133)
('komend', 124)
('projek', 97)
('raport', 84)
('wyjasn', 68)
('chce', 61)
('zmieni', 57)
('konfig', 45)
('jakie', 43)
('kontyn', 41)
('liste', 41)
('sa', 31)
('w', 27)
('funkcj', 26)
('dzien', 25)
('dobry', 25)
('dostep', 25)
('to', 24)
('mozesz', 22)
('repozy', 21)
('nie', 21)
('pomoc', 19)
('tak', 17)
('a', 16)
('czym', 16)
('moge', 15)
('chcial', 14)
('jeszcz', 12)
('dzieku', 12)
('ggphjd', 12)
('o', 11)
('jak', 10)
('witam', 9)
('co', 9)
('mnie', 9)
('repo', 9)
('wszyst', 9)
('z', 9)
('capric', 9)
('qgphjd', 9)
('lista', 9)
('sie', 8)
('system', 8)
('widam', 8)
('inny', 8)
('zglos', 8)
('blad', 8)
('exit', 8)
('inform', 7)
('adawda', 7)
('qwdqwd', 7)
('qgphjs', 7)
('nic', 7)
('tych', 7)
('intere', 7)
('ok', 6)
('mam', 6)
('nowe', 6)
('podaj', 6)
('do', 6)
('powied', 6)
('czesc', 6)
('qgphid', 6)
('dialog', 6)
('qgphj', 6)
('zajeci', 5)
('issue', 5)
('jest', 5)
('pr', 5)
('pgphjd', 5)
('napraw', 5)
('bylem', 5)
('botem', 5)
('i', 5)
('zle', 5)
('przepi', 5

In [13]:
train_size = int(prep.shape[0] * 0.70)

validation_size = int(prep.shape[0] * 0.85)

train_sentences = prep.Wypowiedź[:train_size]
train_labels = prep.Act[:train_size]

test_sentences = prep.Wypowiedź[train_size:validation_size]
test_labels = prep.Act[train_size:validation_size]

validation_sentences = prep.Wypowiedź[validation_size:]
validation_labels = prep.Act[validation_size:]

In [14]:
train = pd.concat([train_sentences, train_labels], ignore_index=False, axis=1)
test = pd.concat([test_sentences, test_labels], ignore_index=False, axis=1)
validation = pd.concat([validation_sentences, validation_labels], ignore_index=False, axis=1)

train, test
# pd.Series(array) 

(                         Wypowiedź  \
 0                            czesc   
 1                 chcial odrzuc pr   
 2                           capric   
 3               oki to bedzie tyle   
 4                           qgphjd   
 ..                             ...   
 408                    o tym samym   
 409                         pgphjd   
 410  pokaz mi raport projek adawda   
 411  w czym jeszcz mozesz mi pomoc   
 412          opowie mi o zajeci ai   
 
                                                    Act  
 0    [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...  
 1    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, ...  
 2    [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
 3    [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
 4    [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
 ..                                                 ...  
 408  [0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
 409  [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
 410  [0

In [15]:
from keras.preprocessing.text import Tokenizer

tokenizer = Tokenizer(num_words=num_words)
tokenizer.fit_on_texts(train['Wypowiedź'])

In [16]:
word_index = tokenizer.word_index

In [17]:
test['Wypowiedź']

413     pokaz mi lista komend
414                    qgphjd
415     pokaz mi liste komend
416                    qgphjs
417    jakie sa dostep funkcj
                ...          
497                    kontyn
498               chce kontyn
499                     czesc
500                    kontyn
501               chce kontyn
Name: Wypowiedź, Length: 89, dtype: object

In [18]:
# train['Wypowiedź'] = train['Wypowiedź'].apply(func = lambda row : tokenizer.texts_to_matrix(tokenizer.texts_to_sequences(row))) 
# test['Wypowiedź'] = test['Wypowiedź'].apply(func = lambda row : tokenizer.texts_to_matrix(tokenizer.texts_to_sequences(row))) 


# train['Wypowiedź'] = train['Wypowiedź'].apply(tokenizer.texts_to_matrix(train['Wypowiedź']))#.apply(func = lambda row : tokenizer.texts_to_matrix(tokenizer.texts_to_sequences(row))) 
# test['Wypowiedź'] = test['Wypowiedź'].apply(func = lambda row : tokenizer.texts_to_matrix(tokenizer.texts_to_sequences(row))) 
train['Wypowiedź'] = (tokenizer.texts_to_sequences(train['Wypowiedź']))
test['Wypowiedź'] = (tokenizer.texts_to_sequences(test['Wypowiedź']))
validation['Wypowiedź'] = (tokenizer.texts_to_sequences(validation['Wypowiedź']))

In [19]:
# train[train['Wypowiedź'].str.len() == 1]
train['Wypowiedź'][5]

[69]

In [20]:
len(train['Wypowiedź'][5]), len(train['Wypowiedź'][200])

(1, 4)

In [21]:
# type(train['Wypowiedź'][0]),type(test['Wypowiedź'][588]),type(train['Act'][0]),type(test['Act'][588])

In [22]:
from keras.preprocessing.sequence import pad_sequences

temp_a = pad_sequences(
    train['Wypowiedź'].tolist(), maxlen=max_len, padding="post", truncating="post"
)
temp_b = pad_sequences(
    test['Wypowiedź'].tolist(), maxlen=max_len, padding="post", truncating="post"
)
temp_c = pad_sequences(
    validation['Wypowiedź'].tolist(), maxlen=max_len, padding="post", truncating="post"
)
train['Wypowiedź'] = temp_a.tolist()
test['Wypowiedź'] = temp_b.tolist()
validation['Wypowiedź'] = temp_c.tolist()

# train=train.reshape(1,train.shape[0])
# mel=mel.reshape(1,mel.shape[0])

# train['Wypowiedź'] = train['Wypowiedź'].apply(lambda row : pad_sequences(
#     row, maxlen=max_len, padding="post", truncating="post"
# ))
# test['Wypowiedź'] = test['Wypowiedź'].apply(lambda row : pad_sequences(
#     row, maxlen=max_len, padding="post", truncating="post"
# )) 

In [23]:
test['Wypowiedź']

413    [2, 1, 34, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...
414    [40, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...
415    [2, 1, 12, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...
416    [67, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...
417    [10, 13, 17, 16, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...
                             ...                        
497    [9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...
498    [7, 9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...
499    [58, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...
500    [9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...
501    [7, 9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...
Name: Wypowiedź, Length: 89, dtype: object

In [24]:
import keras
early_stopping = keras.callbacks.EarlyStopping(
    monitor="val_loss", patience=5, restore_best_weights=True, verbose=0
)

# checkpoint_callback = keras.callbacks.ModelCheckpoint(
#         filepath='.', monitor='val_loss', verbose=0, save_weights_only=True,
#         save_freq='epoch', mode='auto', save_best_only=True)

reduce_lr_on_plateau = keras.callbacks.ReduceLROnPlateau(
    monitor="acc", factor=0.1, patience=2, verbose=0
)

callbacks_list = [early_stopping, reduce_lr_on_plateau]

In [25]:
test

Wypowiedź  \
413  [2, 1, 34, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
414  [40, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
415  [2, 1, 12, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
416  [67, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
417  [10, 13, 17, 16, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
..                                                 ...   
497  [9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
498  [7, 9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
499  [58, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,...   
500  [9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
501  [7, 9, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                                   Act  
413  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, ...  
414  [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
415  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, ...  
416  [1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...  
417  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, ...  
..                                                 ...  
497  [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, ...  
498  [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, ...  
499  [0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...  
500  [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, ...  
501  [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, ...  

[89 rows x 2 columns]

In [26]:
# train['Wypowiedź'] = train['Wypowiedź'].tolist()
# test['Wypowiedź'] = test['Wypowiedź'].tolist()

train['Wypowiedź'] = train['Wypowiedź'].apply(lambda row: np.asarray(row).astype('float32'))
test['Wypowiedź'] = test['Wypowiedź'].apply(lambda row : np.asarray(row).astype('float32'))
validation['Wypowiedź'] = validation['Wypowiedź'].apply(lambda row : np.asarray(row).astype('float32'))

train['Act'] = train['Act'].apply(lambda row : np.asarray(row).astype('float32'))
test['Act'] = test['Act'].apply(lambda row : np.asarray(row).astype('float32'))
validation['Act'] = validation['Act'].apply(lambda row : np.asarray(row).astype('float32'))

In [27]:
# train['Wypowiedź'] = train['Wypowiedź'].apply(lambda row: tf.convert_to_tensor(np.asarray(row).astype('float32')))
# test['Wypowiedź'] = test['Wypowiedź'].apply(lambda row : tf.convert_to_tensor(np.asarray(row).astype('float32')))

# train['Act'] = train['Act'].apply(lambda row : tf.convert_to_tensor(np.asarray(row).astype('float32')))
# test['Act'] = test['Act'].apply(lambda row : tf.convert_to_tensor(np.asarray(row).astype('float32')))


In [28]:
 train['Wypowiedź'][2]

array([60.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.], dtype=float32)

In [29]:
type(train['Wypowiedź']),type(test['Wypowiedź']),type(train['Act']),type(test['Act'])

(pandas.core.series.Series,
 pandas.core.series.Series,
 pandas.core.series.Series,
 pandas.core.series.Series)

In [30]:
train_x = tf.convert_to_tensor(train['Wypowiedź'].tolist())
train_y = tf.convert_to_tensor(train['Act'].tolist())
test_x = tf.convert_to_tensor(test['Wypowiedź'].tolist())
test_y = tf.convert_to_tensor(test['Act'].tolist())

validation_x = tf.convert_to_tensor(validation['Wypowiedź'].tolist())
validation_y = tf.convert_to_tensor(validation['Act'].tolist())

In [31]:
len(validation_y)

89

In [32]:
train_x[0]

<tf.Tensor: shape=(53,), dtype=float32, numpy=
array([58.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.], dtype=float32)>

In [33]:
# # import keras_tuner as kt
# from tensorflow.keras.models import Sequential
# from tensorflow.keras.layers import (
#     Flatten,
#     Dense,
#     Embedding,
#     Conv1D,
#     GlobalMaxPooling1D,
#     MaxPooling1D,
# )


# model = Sequential()
# model.add(
#     Embedding(
#         num_words,
#         output_dim=128,
#         input_length=max_len,
#     )
# )
# model.add(
#     Conv1D(
#         filters=64,
#         kernel_size=3,
#         padding="same",
#         activation="relu",
#         strides=1,
#     )
# )
# model.add(MaxPooling1D(pool_size=2, padding='same'))
# model.add(Flatten())
# model.add(
#     Dense(
#         units=128,
#         activation="relu",
#     )
# )
# model.add(
#     Dense(
#         units=128,
#         activation="relu",
#     )
# )   
# model.add(Dense(10, activation="softmax"))
# model.compile(optimizer="rmsprop", loss="categorical_crossentropy", metrics=["acc"])
# ########################################units????
# model.summary()
# # build_model(kt.HyperParameters())

In [34]:
  tf.shape(train_x[0]), tf.shape(train_y[0]), tf.shape(test_x[0]), tf.shape(test_y[0]),


(<tf.Tensor: shape=(1,), dtype=int32, numpy=array([53])>,
 <tf.Tensor: shape=(1,), dtype=int32, numpy=array([10])>,
 <tf.Tensor: shape=(1,), dtype=int32, numpy=array([53])>,
 <tf.Tensor: shape=(1,), dtype=int32, numpy=array([10])>)

In [35]:
# model.fit(train_x, train_y,  validation_data=(test_x, test_y), callbacks=callbacks_list, verbose=1, epochs=100)


In [36]:
import keras_tuner as kt
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import (
    Flatten,
    Dense,
    Embedding,
    Conv1D,
    GlobalMaxPooling1D,
    MaxPooling1D,
)


def build_model(hp):

    model = Sequential()
    model.add(
        Embedding(
            num_words,
            output_dim=hp.Int("output_dim", min_value=128, max_value=1024, step=128),
            input_length=max_len,
        )
    )
    model.add(
        Conv1D(
            filters=hp.Int("filters0", min_value=64, max_value=512, step=64),
            kernel_size=hp.Int("kernel_size0", min_value=1, max_value=3, step=1),
            padding="same",
            activation="relu",
            strides=hp.Int("strides0", min_value=1, max_value=4, step=1),
        )
    )
    model.add(MaxPooling1D(pool_size=2, padding='same'))
    if hp.Boolean("conv1"):
        model.add(
            Conv1D(
                filters=hp.Int("filters1", min_value=32, max_value=256, step=32),
                kernel_size=hp.Int("kernel_size1", min_value=1, max_value=3, step=1),
                padding="same",
                activation="relu",
                strides=hp.Int("strides1", min_value=1, max_value=4, step=1),
            )
        )
        model.add(MaxPooling1D(pool_size=2, padding='same'))
    model.add(Flatten())
    model.add(
        Dense(
            units=hp.Int("units0", min_value=128, max_value=512, step=64),
            activation="relu",
        )
    )
#     if hp.Boolean("dense1"):
    model.add(
        Dense(
            units=hp.Int("units1", min_value=64, max_value=512, step=64),
            activation="relu",
        )
    )
    if hp.Boolean("dense2"):
        model.add(
            Dense(
                units=hp.Int("units2", min_value=64, max_value=256, step=32),
                activation="relu",
            )
        )    
    model.add(Dense(10, activation="softmax"))
    model.compile(optimizer="rmsprop", loss="binary_crossentropy", metrics=["acc"])
    return model
########################################units????


# model.add(GlobalMaxPooling1D())
# model.compile(optimizer="rmsprop", loss="binary_crossentropy", metrics=["acc"])
# model.summary()
    build_model(kt.HyperParameters())

In [37]:
tuner = kt.Hyperband(
    build_model,
    "val_loss",
    30,
    factor=3,
    hyperband_iterations=3,
)

In [38]:
tuner.search(train_x, train_y,  validation_data=(test_x, test_y), callbacks=callbacks_list, verbose=1)


Trial 270 Complete [00h 00m 05s]
val_loss: 0.045697689056396484

Best val_loss So Far: 0.03326363489031792
Total elapsed time: 00h 20m 11s
INFO:tensorflow:Oracle triggered exit


In [39]:
best_hps=tuner.get_best_models(num_models=1)
# model = tuner.hypermodel.build(best_hps)
best_hps[0]

In [42]:
best_hps[0].evaluate(validation_x, validation_y, batch_size=128)

1/1 [==============================] - 0s 30ms/step - loss: 0.2305 - acc: 0.8315


[0.23047222197055817, 0.8314606547355652]

In [41]:
# model.save(classification.h5)